# Προγραμματιστικά Εργαλεία και Τεχνολογίες για Επιστήμη Δεδομένων
Παράδοση 26/9/2019, Νίκος Παπασπύρου

## Πρόβλημα: Ο λύκος, η κατσίκα και το λάχανο

Δείτε την [περιγραφή του](https://en.wikipedia.org/wiki/Fox,_goose_and_bag_of_beans_puzzle).

Η κλάση που υλοποιεί τις καταστάσεις.

In [1]:
class state:
    def __init__(self, left, right):
        self.left = frozenset(left)
        self.right = frozenset(right)
    def __str__(self):
        return "{} | {}".format(" ".join(self.left),
                                " ".join(self.right))
    def success(self):
        return not self.left
    def safe(self):
        def tragic(bank):
            return "man" not in bank and "goat" in bank and \
                ("cabbage" in bank or "wolf" in bank)
        return not tragic(self.left) and not tragic(self.right)
    def accessible(self):
        if 'man' in self.left:
            for x in self.left:
                moving = frozenset(['man', x])
                yield state(self.left - moving,
                            self.right | moving)
        else:
            for x in self.right:
                moving = frozenset(['man', x])
                yield state(self.left | moving,
                            self.right - moving)
                
    # Αυτό χρειάζεται για να μπορούμε να συγκρίνουμε αν δύο καταστάσεις είναι ίσες.
    def __eq__(self, other):
        return self.left == other.left
    # Αυτό χρειάζεται για να μπορούμε να προσθέτουμε καταστάσεις σε σύνολα και λεξικά.
    def __hash__(self):
        return hash(self.left)
    # Χωρίς αυτά τα δύο, η έκδοση του αλγόριθμου αναζήτησης παρακάτω που προσπαθεί
    # να θυμάται αν έχουμε ή όχι επισκεφθεί κάποια κατάσταση δε θα δούλευε σωστά,
    # καθώς θα μπερδευόταν από διαφορετικά αντικείμενα που παριστάνουν ίσες καταστάσεις.

In [2]:
init = state(["man", "wolf", "goat", "cabbage"], [])

In [3]:
str(init)

'man goat cabbage wolf | '

In [4]:
init.success()

False

In [5]:
init.safe()

True

In [6]:
state(["wolf", "goat"], ["man", "cabbage"]).safe()

False

In [7]:
for s in init.accessible():
    if s.safe():
        print(s)

cabbage wolf | man goat


Ο αλγόριθμος αναζήτησης στο χώρο καταστάσεων.  Πρώτη έκδοση, δεν ελέγχει αν επιστρέφουμε σε καταστάσεις που τις έχουμε ήδη επισκεφθεί.

In [8]:
from collections import deque

In [9]:
def solve():
    init = state(["man", "wolf", "goat", "cabbage"], [])
    Q = deque()
    Q.append(init)
    while Q:
        s = Q.popleft()
        for t in s.accessible():
            if t.success():
                return t
            elif t.safe():
                Q.append(t)

In [10]:
print(solve())

 | man goat cabbage wolf


Δεύτερη έκδοση, ελέγχει αν έχουμε ήδη επισκεφθεί κάποια κατάσταση.

In [11]:
def solve():
    init = state(["man", "wolf", "goat", "cabbage"], [])
    Q = deque()
    seen = set()
    Q.append(init)
    seen.add(init)
    while Q:
        s = Q.popleft()
        for t in s.accessible():
            if t.success():
                return t
            elif t.safe() and t not in seen:
                Q.append(t)
                seen.add(t)

In [12]:
print(solve())

 | man goat cabbage wolf


Λίγα πράγματα για hashing...

In [13]:
hash(42)

42

In [14]:
hash("hello"), hash("hellx")

(3813657663198258469, -5908719058881407075)

In [15]:
(hash(frozenset([1, 5, 8, 10])),
 hash(frozenset([5,8]) | frozenset([10, 1])))

(8675845919982142549, 8675845919982142549)

In [16]:
hash((14, "hello", False))

7239731701927232972

In [17]:
hash((1, 2, 3)), hash((2, 3, 1))

(2528502973977326415, 3789705017590651805)

Τρίτη έκδοση, για κάθε κατάσταση θυμάται την προηγούμενη έτσι ώστε να μπορούμε να εκτυπώσουμε την τελική λύση.

In [18]:
def solve():
    init = state(["man", "wolf", "goat", "cabbage"], [])
    Q = deque()
    seen = {}
    Q.append(init)
    seen[init] = None
    while Q:
        s = Q.popleft()
        for t in s.accessible():
            if t.success():
                seen[t] = s
                def solution(s):
                    p = seen[s]
                    if p is None: return [s]
                    return solution(p) + [s]                
                return solution(t)
            elif t.safe() and t not in seen:
                Q.append(t)
                seen[t] = s

In [19]:
for s in solve():
    print(s)

man goat cabbage wolf | 
cabbage wolf | man goat
man cabbage wolf | goat
wolf | goat cabbage man
man goat wolf | cabbage
goat | man cabbage wolf
goat man | cabbage wolf
 | man goat cabbage wolf


## NumPy

In [20]:
import numpy as np

In [21]:
a = np.array([1, 2, 3])

In [22]:
a

array([1, 2, 3])

In [23]:
print(a)

[1 2 3]


In [24]:
type(a)

numpy.ndarray

In [25]:
a.ndim

1

In [26]:
a.shape

(3,)

In [27]:
a[1]

2

In [28]:
a[1] = 42

In [29]:
print(a)

[ 1 42  3]


In [30]:
b = np.array([[1, 2, 3], [4, 5, 6]])

In [31]:
print(b)

[[1 2 3]
 [4 5 6]]


In [32]:
type(b)

numpy.ndarray

In [33]:
b.ndim

2

In [34]:
b.shape

(2, 3)

In [35]:
b[0][1]

2

In [36]:
b[0, 1]

2

In [37]:
b[0, 1] = 17

In [38]:
print(b)

[[ 1 17  3]
 [ 4  5  6]]


In [39]:
print(b[0])

[ 1 17  3]


In [40]:
b[0].shape

(3,)

In [41]:
type(b[0])

numpy.ndarray

In [42]:
for x in b:
    print(x)

[ 1 17  3]
[4 5 6]


In [43]:
for x in a:
    print(x)

1
42
3


In [44]:
for x in b.flat:
    print(x)

1
17
3
4
5
6


In [45]:
b.dtype

dtype('int64')

In [46]:
c = np.array([3.14, 2.78])

In [47]:
print(c)

[3.14 2.78]


In [48]:
c.dtype

dtype('float64')

In [49]:
z = np.zeros((3, 3))

In [50]:
print(z)

[[0. 0. 0.]
 [0. 0. 0.]
 [0. 0. 0.]]


In [51]:
print(np.zeros((3, 3), dtype=np.int64))

[[0 0 0]
 [0 0 0]
 [0 0 0]]


In [52]:
z[1,1] = 42

In [53]:
print(z)

[[ 0.  0.  0.]
 [ 0. 42.  0.]
 [ 0.  0.  0.]]


In [54]:
print(b)

[[ 1 17  3]
 [ 4  5  6]]


In [55]:
b[1,1] = 3.14

In [56]:
print(b)

[[ 1 17  3]
 [ 4  3  6]]


In [57]:
n = np.ones((3, 3))

In [58]:
print(n)

[[1. 1. 1.]
 [1. 1. 1.]
 [1. 1. 1.]]


In [59]:
f = np.full((3, 3), 42)

In [60]:
print(f)

[[42 42 42]
 [42 42 42]
 [42 42 42]]


In [61]:
i = np.eye(3)

In [62]:
print(i)

[[1. 0. 0.]
 [0. 1. 0.]
 [0. 0. 1.]]


In [63]:
print(np.arange(10))

[0 1 2 3 4 5 6 7 8 9]


In [64]:
print(np.arange(4, 10))

[4 5 6 7 8 9]


In [65]:
print(np.arange(4, 10, 2))

[4 6 8]


In [66]:
r = np.random.random((3, 3))

In [67]:
print(r)

[[0.08133639 0.06644578 0.47270421]
 [0.4815129  0.13011649 0.56287027]
 [0.71039551 0.90870726 0.47106943]]


In [68]:
print("{:0.15f}".format(r[0,0]))

0.081336391725863


In [69]:
print("{:0.100f}".format(r[0,0]))

0.0813363917258628221773619770829100161790847778320312500000000000000000000000000000000000000000000000


In [70]:
print(i)

[[1. 0. 0.]
 [0. 1. 0.]
 [0. 0. 1.]]


In [71]:
print(i[:2, 1:3])

[[0. 0.]
 [1. 0.]]


In [72]:
s = i[:2, 1:3]

In [73]:
print(s)

[[0. 0.]
 [1. 0.]]


In [74]:
s[1, 0]

1.0

In [75]:
s[1, 0] = 42

In [76]:
print(s)

[[ 0.  0.]
 [42.  0.]]


In [77]:
print(i)

[[ 1.  0.  0.]
 [ 0. 42.  0.]
 [ 0.  0.  1.]]


In [78]:
c = i[:2, 1:3].copy()

In [79]:
print(c)

[[ 0.  0.]
 [42.  0.]]


In [80]:
c[1, 0] = 17

In [81]:
print(c)

[[ 0.  0.]
 [17.  0.]]


In [82]:
print(i)

[[ 1.  0.  0.]
 [ 0. 42.  0.]
 [ 0.  0.  1.]]


In [83]:
print(i[1, 1:3])

[42.  0.]


In [84]:
i = np.eye(3)

In [85]:
print(i)

[[1. 0. 0.]
 [0. 1. 0.]
 [0. 0. 1.]]


In [86]:
x = np.arange(3)

In [87]:
print(x)

[0 1 2]


In [88]:
y = np.array([2, 0, 1])

In [89]:
print(y)

[2 0 1]


In [90]:
print(i[x, y])

[0. 0. 0.]


In [91]:
i[x, y] += 5

In [92]:
print(i)

[[1. 0. 5.]
 [5. 1. 0.]
 [0. 5. 1.]]


In [93]:
j = i > 0

In [94]:
print(j)

[[ True False  True]
 [ True  True False]
 [False  True  True]]


In [95]:
print(i[j])

[1. 5. 5. 1. 5. 1.]


In [96]:
print(i[i==5])

[5. 5. 5.]


In [97]:
i[i==5] = 42

In [98]:
print(i)

[[ 1.  0. 42.]
 [42.  1.  0.]
 [ 0. 42.  1.]]


In [99]:
print(x)

[0 1 2]


In [100]:
print(y)

[2 0 1]


In [101]:
print(x+y)

[2 1 3]


In [102]:
print(x*y)

[0 0 2]


In [103]:
print(np.dot(x, y))

2


In [104]:
print(x @ y)

2


In [105]:
print(np.sqrt(x))

[0.         1.         1.41421356]


In [106]:
print(i)

[[ 1.  0. 42.]
 [42.  1.  0.]
 [ 0. 42.  1.]]


In [107]:
print(np.transpose(i))

[[ 1. 42.  0.]
 [ 0.  1. 42.]
 [42.  0.  1.]]


In [108]:
print(i.T)

[[ 1. 42.  0.]
 [ 0.  1. 42.]
 [42.  0.  1.]]


In [109]:
i.T[0, 1] = 17

In [110]:
print(i)

[[ 1.  0. 42.]
 [17.  1.  0.]
 [ 0. 42.  1.]]


In [111]:
print(np.linalg.inv(i))

[[ 3.33455600e-05  5.88215679e-02 -1.40051352e-03]
 [-5.66874521e-04  3.33455600e-05  2.38087299e-02]
 [ 2.38087299e-02 -1.40051352e-03  3.33455600e-05]]


In [112]:
x = np.array([[1,2,3], [4,5,6], [7,8,9], [10,11,12]])

In [113]:
print(x)

[[ 1  2  3]
 [ 4  5  6]
 [ 7  8  9]
 [10 11 12]]


In [114]:
v = np.array([1, 0, 1])

In [115]:
print(v)

[1 0 1]


In [116]:
y = np.empty_like(x)

In [117]:
for i in range(4):
    y[i] = x[i] + v

In [118]:
print(y)

[[ 2  2  4]
 [ 5  5  7]
 [ 8  8 10]
 [11 11 13]]


In [119]:
print(v)

[1 0 1]


In [120]:
z = np.tile(v, (4, 1))

In [121]:
print(z)

[[1 0 1]
 [1 0 1]
 [1 0 1]
 [1 0 1]]


In [122]:
print(np.tile(v, (2, 3)))

[[1 0 1 1 0 1 1 0 1]
 [1 0 1 1 0 1 1 0 1]]


In [123]:
print(x)

[[ 1  2  3]
 [ 4  5  6]
 [ 7  8  9]
 [10 11 12]]


In [124]:
print(z)

[[1 0 1]
 [1 0 1]
 [1 0 1]
 [1 0 1]]


In [125]:
print(x + z)

[[ 2  2  4]
 [ 5  5  7]
 [ 8  8 10]
 [11 11 13]]


In [126]:
print(x + v)

[[ 2  2  4]
 [ 5  5  7]
 [ 8  8 10]
 [11 11 13]]


In [127]:
print(x + 1)

[[ 2  3  4]
 [ 5  6  7]
 [ 8  9 10]
 [11 12 13]]


In [128]:
a = np.arange(15)

In [129]:
print(a)

[ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14]


In [130]:
s = a.reshape(3, 5)

In [131]:
print(s)

[[ 0  1  2  3  4]
 [ 5  6  7  8  9]
 [10 11 12 13 14]]


In [132]:
s[1,1] = 42

In [133]:
print(s)

[[ 0  1  2  3  4]
 [ 5 42  7  8  9]
 [10 11 12 13 14]]


In [134]:
print(a)

[ 0  1  2  3  4  5 42  7  8  9 10 11 12 13 14]
